# Data Processing and Preparation from Excel to Training and Testing Sets

data in under `data/202403010927.xlsx, data/202403080504.xlsx, data/202403080515.xlsx `

In [37]:
import pandas as pd
import requests
import os
import concurrent.futures

## Data Downloading

The total number of htmls are 381823, after downloading we have xxx pairs.

After filtering the wrong/404 ones, we have .

In [30]:
data = []
# 读取 Excel 文件
file_1, file_2, file_3 = 'data/202403010927.xlsx', 'data/202403080504.xlsx', 'data/202403080515.xlsx'
df_1 = pd.read_excel(file_1)
data.extend(df_1['html_file,"json_file","json_block_file","source_url"'].tolist())
df_2 = pd.read_excel(file_2)
data.extend(df_2['html_file,"json_file","json_block_file","source_url"'].tolist())
df_3 = pd.read_excel(file_3)
data.extend(df_3['html_file,"json_file","json_block_file","source_url"'].tolist())

len(data)

381823

In [44]:
os.makedirs('html', exist_ok=True)
os.makedirs('gt', exist_ok=True)

def download_url(url, directory):
    try:
        response = requests.get(url)
        response.raise_for_status()  # 如果请求失败，抛出HTTPError
        file_name = url.split('/')[-1]
        file_path = os.path.join(directory, file_name)
        with open(file_path, 'wb') as file:
            file.write(response.content)
        return file_path, None
    except requests.RequestException as e:
        return url, str(e)
    
def download_all(data):
    results = []
    with concurrent.futures.ThreadPoolExecutor(max_workers=5) as executor:
        futures = []
        for urls in data:
            urls = urls.split(',')
            if len(urls) < 2:
                continue
            html_url, gt_url = urls[:2]

            futures.append(executor.submit(download_url, html_url, 'html'))
            futures.append(executor.submit(download_url, gt_url, 'gt'))

        for future in concurrent.futures.as_completed(futures):
            result, error = future.result()
            if error:
                print(f"Failed to download: {result} - Error: {error}")
            else:
                print(f"Downloaded: {result}")

download_all(data)


Failed to download: http://storage.static-green-acres.com/domains/squarehabitat.fr/adverts_html/egjt5mjw18q8qjo6yghegv2i4j02bgvn.html - Error: 502 Server Error: Bad Gateway for url: http://storage.static-green-acres.com/domains/squarehabitat.fr/adverts_html/egjt5mjw18q8qjo6yghegv2i4j02bgvn.html
Downloaded: html/q2x4t9k8lcjkhirtlad3zu1n64ves9kc.html
Downloaded: html/bx00odawc7zohbt0z2n2smixy61i65p1.html
Downloaded: html/hg8n95wl4www4iolweaalhu6quoc3uho.html
Downloaded: gt/bx00odawc7zohbt0z2n2smixy61i65p1.json
Downloaded: gt/axsk9nu52qs650z2ciu89cvh6xtelns1.json
Failed to download: http://storage.static-green-acres.com/domains/repimmo.com/adverts_html/j3dphq3cevyt6qz7y9kb8e5b9rgxk92s.html - Error: 502 Server Error: Bad Gateway for url: http://storage.static-green-acres.com/domains/repimmo.com/adverts_html/j3dphq3cevyt6qz7y9kb8e5b9rgxk92s.html
Downloaded: html/skcd9xctbqryvog6muniv6f87x6z27kv.html
Downloaded: gt/hg8n95wl4www4iolweaalhu6quoc3uho.json
Downloaded: html/ijsjdfqvohr1k54j48kqzc